In [5]:
import os, json
from collections import defaultdict
import customutils

alphapose_labels = customutils.get_classes('configs/halpe26_classes.txt')
openpose_labels = customutils.get_classes('configs/openpose_classes.txt')
vitpose_labels = customutils.get_classes('configs/cocowb_classes.txt')
coco_labels = customutils.get_classes('configs/coco_classes.txt')
mpii_labels = customutils.get_classes('configs/mpii_classes.txt')


coco_categories = [
        {
            "supercategory": "person",
            "id": 1,
            "name": "person",
            "keypoints": ["nose", "left_eye", "right_eye", "left_ear", "right_ear", "left_shoulder", "right_shoulder", "left_elbow", "right_elbow", "left_wrist", "right_wrist", "left_hip", "right_hip", "left_knee", "right_knee", "left_ankle", "right_ankle"],
            "skeleton": [[16, 14], [14, 12], [17, 15], [15, 13], [12, 13], [6, 12], [7, 13], [6, 7], [6, 8], [7, 9], [8, 10], [9, 11], [2, 3], [1, 2], [1, 3], [2, 4], [3, 5], [4, 6], [5, 7]]
        }
    ]

halpe_categories = [
        {
            "supercategory": "person",
            "id": 1,
            "name": "person",
            "keypoints": ["nose", "left_eye", "right_eye", "left_ear", "right_ear", "left_shoulder", "right_shoulder", "left_elbow", "right_elbow", "left_wrist", "right_wrist", "left_hip", "right_hip", "left_knee", "right_knee", "left_ankle", "right_ankle", "head", "neck", "hip", "left_big_toe", "right_big_toe", "left_small_toe", "right_small_toe", "left_heel", "right_heel"],
            "skeleton": [[16, 14], [14, 12], [17, 15], [15, 13], [12, 13], [6, 12], [7, 13], [6, 7], [6, 8], [7, 9], [8, 10], [9, 11], [2, 3], [1, 2], [1, 3], [2, 4], [3, 5], [4, 6], [5, 7]]
        }
    ]

In [6]:
def get_coco_pose(pose, src_labels, dest_labels, videoId):
    joints = defaultdict(list)
    imgId = int(pose['image_id'].replace('COCO_test2015_','').replace('COCO_val2014_','').replace('.jpg',''))
    if videoId > 0:
        imgId = videoId
    pose['image_id'] = imgId

    keypoints_index = 0
    keypoints = pose['keypoints']
    conf_total = 0
    for label in src_labels:
        joints[label] = {'x': keypoints[keypoints_index], 'y': keypoints[keypoints_index+1], 'confidence': keypoints[keypoints_index+2]}
        conf_total += keypoints[keypoints_index+2]
        keypoints_index += 3

    dest_keypoints = []
    for label in dest_labels:
        if label in joints:
            dest_keypoints.append(joints[label]['x'])
            dest_keypoints.append(joints[label]['y'])
            dest_keypoints.append(2)
        else:
            dest_keypoints.append(0)
            dest_keypoints.append(0)
            dest_keypoints.append(1)

    pose['keypoints'] = dest_keypoints
    pose['score'] = conf_total/len(src_labels)
    return pose

def get_mpii_pose(pose, labels):
    joints = defaultdict(list)
    imgId = int(pose['image_id'].replace('COCO_test2015_','').replace('COCO_val2014_','').replace('.jpg',''))
    pose['image_id'] = imgId

    keypoints_index = 0
    keypoints = pose['keypoints']
    for label in labels:
        if label in mpii_labels:
            joints[label] = {'id': customutils.get_id_by_name(mpii_labels, label), 'x': keypoints[keypoints_index], 'y': keypoints[keypoints_index+1], 'score': keypoints[keypoints_index+2]}
        keypoints_index += 3

    for label in mpii_labels:
        if len(joints[label]) == 0:
            joints[label] = {'id': customutils.get_id_by_name(mpii_labels, label) ,'x': 0, 'y': 0, 'score': 0}
    
    annopoints = {'annopoints': list(joints.values())}
    return annopoints

In [4]:
# COCO: AlphaPose
file_path = '../data/output/alphapose/coco/val2014/'
res_path = '../data/coco/results/alphapose/person_keypoints_val2014_2.json'
all_Results = []
full_file = file_path + 'alphapose-results.json'
# for filename in os.listdir(file_path):
    # full_file = os.path.join(file_path, filename) + '/alphapose-results.json'
with open(full_file, 'r') as f:
    predictions_annotations = json.load(f)
    for pose in predictions_annotations:      
        alphapose_pose = get_coco_pose(pose, alphapose_labels, coco_labels, -1)  
        alphapose_pose['score'] = 1
        all_Results.append(alphapose_pose)
    
    
customutils.writeJson(all_Results,res_path)

In [16]:
# MPII: AlphaPose
file_path = '../data/output/alphapose/mpii'
res_path = '../data/mpii/results/alphapose/preds.json'
all_Results = []
for filename in os.listdir(file_path):
    full_file = os.path.join(file_path, filename) + '/alphapose-results.json'
    with open(full_file, 'r') as f:
        predictions_annotations = json.load(f)
        annorect = []
        for pose in predictions_annotations:      
            annopoints = get_mpii_pose(pose, alphapose_labels, coco_labels)  
            annorect.append(annopoints)
        annolist = {'image_name': filename + '.jpg', 'annorect': annorect}
        all_Results.append(annolist)
    
    
customutils.writeJson(all_Results,res_path)

In [29]:
# COCO: ViTPose
file_path = '../data/output/ViTPose/coco/val2017/'
res_path = '../data/coco/results/ViTPose/person_keypoints_val2017.json'
all_Results = []
for filename in os.listdir(file_path):
    if filename.endswith('.json'):
        full_file = os.path.join(file_path, filename)
        with open(full_file, 'r') as f:
            predictions_annotations = json.load(f)
            for pose in predictions_annotations:  
                vitpose_pose = get_coco_pose(pose, vitpose_labels, coco_labels, -1)
                vitpose_pose['score'] = 1
                vitpose_pose['category_id'] = 1
                all_Results.append(vitpose_pose)
    
    
customutils.writeJson(all_Results,res_path)

In [18]:
# MPII: ViTPose
file_path = '../data/output/ViTPose/mpii/'
res_path = '../data/mpii/results/ViTPose/preds.json'
all_Results = []
for filename in os.listdir(file_path):
    if filename.endswith('.json'):
        full_file = os.path.join(file_path, filename)
        with open(full_file, 'r') as f:
            predictions_annotations = json.load(f)
            for pose in predictions_annotations:  
                annopoints = get_mpii_pose(pose, vitpose_labels)
                annorect.append(annopoints)
        annolist = {'image_name': filename.replace('.json', '.jpg'), 'annorect': annorect}
        all_Results.append(annolist)
    
    
customutils.writeJson(all_Results,res_path)

In [22]:
# COCO: OpenPose
file_path = '../data/output/openpose/coco/val2014'
res_path = '../data/coco/results/openpose/person_keypoints_val2014.json'
all_Results = []
for filename in os.listdir(file_path):
    if filename.endswith('.json'):
      full_file = os.path.join(file_path, filename)
      with open(full_file, 'r') as f:
         predictions_annotations = json.load(f)
         for pose in predictions_annotations['people']:
            joints = defaultdict(list)
            imgId = int(filename.replace('COCO_test2015_','').replace('COCO_val2014_','').replace('_keypoints.json',''))

            keypoints_index = 0
            openpose_keypoints = pose['pose_keypoints_2d']
            for label in openpose_labels:
               joints[label] = {'x': openpose_keypoints[keypoints_index], 'y': openpose_keypoints[keypoints_index+1], 'confidence': openpose_keypoints[keypoints_index+2]}
               keypoints_index += 3

            coco_keypoints = []
            for label in coco_labels:
               coco_keypoints.append(joints[label]['x'])
               coco_keypoints.append(joints[label]['y'])
               coco_keypoints.append(2)

            coco_pose = {'image_id': imgId, 'keypoints': coco_keypoints, 'category_id': 1, 'score': 1}
            all_Results.append(coco_pose)
    #break

customutils.writeJson(all_Results,res_path)

In [8]:
# MPII: OpenPose
file_path = '../data/output/openpose/mpii/json'
res_path = '../data/mpii/results/openpose/preds.json'
all_Results = []
for filename in os.listdir(file_path):
    full_file = os.path.join(file_path, filename)
    with open(full_file, 'r') as f:
        predictions_annotations = json.load(f)
        annorect = []
        for pose in predictions_annotations['people']:
           joints = defaultdict(list)
           imgId = filename.replace('_keypoints.json','.jpg')

           keypoints_index = 0
           openpose_keypoints = pose['pose_keypoints_2d']
           for label in openpose_labels:
              if label in mpii_labels:
                  joints[label] = {'id': customutils.get_id_by_name(mpii_labels, label) ,'x': openpose_keypoints[keypoints_index], 'y': openpose_keypoints[keypoints_index+1], 'score': openpose_keypoints[keypoints_index+2]}
              keypoints_index += 3

           for label in mpii_labels:
              if len(joints[label]) == 0:
                  joints[label] = {'id': customutils.get_id_by_name(mpii_labels, label) ,'x': 0, 'y': 0, 'score': 0}

           annopoints = {'annopoints': list(joints.values())}
           annorect.append(annopoints)

        annolist = {'image_name': imgId, 'annorect': annorect}
        all_Results.append(annolist)

customutils.writeJson(all_Results,res_path)

In [21]:
# Videos annotations

def save_annotations(labels, res_file_name, categories):
    file_path = '../videos/annotations/'
    res_path = '../videos/lite_running_keypoints.json'
    coco_res_path = '../videos/' + res_file_name
    all_Results = []
    all_images = []
    coco_Results = []
    video_count = 1000
    for filename in os.listdir(file_path):
        if filename.endswith('.json'):
            full_file = os.path.join(file_path, filename)
            with open(full_file, 'r') as f:
                predictions_annotations = json.load(f)
                file_name = predictions_annotations['item']['name']
                frame_count = predictions_annotations['item']['slots'][0]['frame_count']
                person_index = 0
                for annot in predictions_annotations['annotations']:
                    
                    for frame_index in range(0, frame_count):
                        if frame_index < len(annot['frames']):
                            points = annot['frames'][str(frame_index)]['skeleton']['nodes']
                            bb = customutils.get_bb_coco(points)
                            area = customutils.compute_area_coco(bb)

                            # Create a dictionary to map 'id' to its position in the order array
                            id_to_index = {id_value: index for index, id_value in enumerate(labels)}

                            # Sort the data based on the custom sorting key
                            sorted_data = sorted(points, key=lambda x: id_to_index.get(x['name'], float('inf')))
                            kpts = []
                            for point in sorted_data:
                                if point['name'] in labels: #check joint is available for this technique
                                    kpts.append(point['x'])
                                    kpts.append(point['y'])

                                    if point["occluded"] == "false":
                                        kpts.append(2)
                                    else:                       
                                        kpts.append(1)
                                        
                            image_id = video_count + frame_index
                            pose_id = video_count + frame_index + person_index*100000
                            all_Results.append({'image_id': image_id, 'pose_id': pose_id, 'file_name': file_name, 'frame': frame_index, 'person': person_index})
                            if person_index == 0:
                                all_images.append({'id': image_id, 'file_name': file_name})
                                
                            coco_Results.append({'id': image_id, 'image_id': image_id, "category_id": 1, "bbox": bb, "area": area, "iscrowd": 1, "num_keypoints": len(labels), "keypoints": kpts})

                    person_index += 1

            video_count += 1000
        
        
    customutils.writeJson(all_Results,res_path)
    customutils.writeJson({"categories":categories,"images":all_images,"annotations":coco_Results},coco_res_path)
    print("Annotations saved to " + coco_res_path)

save_annotations(coco_labels, 'person_keypoints_coco_running.json', coco_categories)
save_annotations(alphapose_labels, 'person_keypoints_running.json', halpe_categories)

Annotations saved to ../videos/person_keypoints_coco_running.json
Annotations saved to ../videos/person_keypoints_running.json


In [8]:
# Load images dataset
import pandas as pd
running_annotations = '../videos/lite_running_keypoints.json'
with open(running_annotations, 'r') as f:
    videos_ids = defaultdict(list)
    annots = json.load(f)
    df_running_annotations = pd.DataFrame(annots)

print(df_running_annotations)

    

      image_id                                         file_name  frame
0         1000               Athletics_Mixed_Tokyo_2020_20_1.mp4      0
1         1001               Athletics_Mixed_Tokyo_2020_20_1.mp4      1
2         1002               Athletics_Mixed_Tokyo_2020_20_1.mp4      2
3         1003               Athletics_Mixed_Tokyo_2020_20_1.mp4      3
4         1004               Athletics_Mixed_Tokyo_2020_20_1.mp4      4
...        ...                                               ...    ...
5586     46160  World_Athletics_Women_Marathon_Oregon_2022_8.mp4    160
5587     46161  World_Athletics_Women_Marathon_Oregon_2022_8.mp4    161
5588     46162  World_Athletics_Women_Marathon_Oregon_2022_8.mp4    162
5589     46163  World_Athletics_Women_Marathon_Oregon_2022_8.mp4    163
5590     46164  World_Athletics_Women_Marathon_Oregon_2022_8.mp4    164

[5591 rows x 3 columns]


In [9]:
# Videos as COCO: AlphaPose
def save_predictions_alphapose(labels, res_file_name):
    file_path = '../data/videos/results/alphapose/'
    res_path = '../videos/results/alphapose/' + res_file_name
    all_Results = []
    for filename in os.listdir(file_path):
        full_file = os.path.join(file_path, filename) + '/alphapose-results.json'
        isExist = os.path.exists(full_file)
        if isExist:
            with open(full_file, 'r') as f:
                predictions_annotations = json.load(f)
                mask_file = df_running_annotations['file_name'] == filename + '.mp4'
                for pose in predictions_annotations:
                    frame_index = int(pose['image_id'].replace('.jpg', ''))
                    mask_frame = df_running_annotations['frame'] == frame_index
                    df = df_running_annotations.loc[mask_file & mask_frame]
                    if len(df) == 0:
                        print('Missing ' + filename + ' frame ' + str(frame_index))
                    else:
                        image_id = df['image_id'].iloc[0]
                        alphapose_pose = get_coco_pose(pose, alphapose_labels, labels, image_id)  
                        new_pose = {}
                        new_pose['image_id'] = int(alphapose_pose['image_id'])
                        new_pose['keypoints'] = alphapose_pose['keypoints']
                        new_pose['score'] = alphapose_pose['score']
                        new_pose['category_id'] = 1
                        all_Results.append(new_pose)
        
        
    customutils.writeJson(all_Results,res_path)
    
save_predictions_alphapose(coco_labels, 'person_keypoints_coco_running.json')
save_predictions_alphapose(alphapose_labels, 'person_keypoints_running.json')

Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 218
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 219
Missing Triathlon_Men_Tokyo_2020_28 frame 220
Missing Triathlon_Men_Tokyo_2020_2

In [10]:
# Videos as COCO: ViTPose
def save_predictions_vitpose(labels, res_file_name):
    file_path = '../data/videos/results/ViTPose/'
    res_path = '../videos/results/ViTPose/' + res_file_name
    all_Results = []
    for filename in os.listdir(file_path):
        if filename.endswith('.json'):
            full_file = os.path.join(file_path, filename)
            with open(full_file, 'r') as f:
                predictions_annotations = json.load(f)
                mask_file = df_running_annotations['file_name'] == filename.replace('.json','')
                for pose in predictions_annotations:  
                    frame_index = int(pose['image_id'].replace('.jpg', ''))
                    mask_frame = df_running_annotations['frame'] == frame_index
                    df = df_running_annotations.loc[mask_file & mask_frame]
                    if len(df) == 0:
                        print('Missing ' + filename + ' frame ' + str(frame_index))
                    else:
                        image_id = df['image_id'].iloc[0]
                        vitpose_pose = get_coco_pose(pose, vitpose_labels, labels, image_id)
                        new_pose = {}
                        new_pose['image_id'] = int(vitpose_pose['image_id'])
                        new_pose['keypoints'] = vitpose_pose['keypoints']
                        new_pose['score'] = vitpose_pose['score']
                        new_pose['category_id'] = 1
                        all_Results.append(new_pose)
        
        
    customutils.writeJson(all_Results,res_path)
    print("Saved ViTPose results to " + res_path)

save_predictions_vitpose(coco_labels, 'person_keypoints_coco_running.json')
save_predictions_vitpose(alphapose_labels, 'person_keypoints_running.json')

Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 218
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 218
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 218
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 218
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 218
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 219
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 219
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 219
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 219
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 219
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 220
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 220
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 220
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 220
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 220
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 221
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 221
Missing Triathlon_Men_Tokyo_2020_28.mp4.json frame 221
Missing Tr

In [18]:
# Videos as COCO: OpenPose
file_path = '../data/videos/results/openpose'
res_path = '../videos/results/openpose/person_keypoints_running.json'
all_Results = []
for root, subdirs, files in os.walk(file_path):
    for filename in files:
      if filename.endswith('.json'):
         full_file = os.path.join(root, filename)
         with open(full_file, 'r') as f:
            predictions_annotations = json.load(f)
            image_name = os.path.basename(root).replace('.json','')
            mask_file = df_running_annotations['file_name'] == image_name + '.mp4'
            frame_index = int(filename.replace(image_name + '_','').replace('_keypoints.json',''))
            mask_frame = df_running_annotations['frame'] == frame_index
            df = df_running_annotations.loc[mask_file & mask_frame]
            if len(df) == 0:
               print('Missing ' + filename + ' frame ' + str(frame_index))
            else:
               imgId = df['image_id'].iloc[0]
               for pose in predictions_annotations['people']:
                  joints = defaultdict(list)

                  keypoints_index = 0
                  openpose_keypoints = pose['pose_keypoints_2d']
                  conf_total = 0
                  for label in openpose_labels:
                     joints[label] = {'x': openpose_keypoints[keypoints_index], 'y': openpose_keypoints[keypoints_index+1], 'confidence': openpose_keypoints[keypoints_index+2]}
                     conf_total += openpose_keypoints[keypoints_index+2]
                     keypoints_index += 3

                  score = conf_total/len(openpose_labels)

                  coco_keypoints = []
                  for label in coco_labels:
                     coco_keypoints.append(joints[label]['x'])
                     coco_keypoints.append(joints[label]['y'])
                     coco_keypoints.append(2)

                  coco_pose = {'image_id': int(imgId), 'keypoints': coco_keypoints, 'category_id': 1, 'score': score}
                  all_Results.append(coco_pose)
    #break

customutils.writeJson(all_Results,res_path)

Missing Triathlon_Men_Tokyo_2020_28_000000000218_keypoints.json frame 218
Missing Triathlon_Men_Tokyo_2020_28_000000000219_keypoints.json frame 219
Missing Triathlon_Men_Tokyo_2020_28_000000000220_keypoints.json frame 220
Missing Triathlon_Men_Tokyo_2020_28_000000000221_keypoints.json frame 221
Missing Triathlon_Men_Tokyo_2020_28_000000000222_keypoints.json frame 222
Missing Triathlon_Men_Tokyo_2020_28_000000000223_keypoints.json frame 223
Missing Triathlon_Men_Tokyo_2020_28_000000000224_keypoints.json frame 224
Missing World_Athletics_Men_10000m_Oregon_2022_12_000000000000_keypoints.json frame 0
Missing World_Athletics_Men_10000m_Oregon_2022_12_000000000001_keypoints.json frame 1
Missing World_Athletics_Men_10000m_Oregon_2022_12_000000000002_keypoints.json frame 2
Missing World_Athletics_Men_10000m_Oregon_2022_12_000000000003_keypoints.json frame 3
Missing World_Athletics_Men_10000m_Oregon_2022_12_000000000004_keypoints.json frame 4
Missing World_Athletics_Men_10000m_Oregon_2022_12_00